In [25]:
import re
import pandas as pd
import funcs 
import importlib
import unicodecsv as csv
from timeit import default_timer as timer
from datetime import datetime, timedelta

importlib.reload(funcs)

<module 'funcs' from 'C:\\Users\\Mag\\Documents\\_projekty\\praca\\funcs.py'>

## 0. Wczytanie danych zrzuconych z bazy SQL do csv

In [2]:
politicians = pd.read_csv("00_dane/portraits.csv", sep='|')
#speeches = pd.read_csv("00_dane/speech_data.csv", sep='|')

#wczytujemy plik po modyfikacjach w SQL
speeches = pd.read_csv("00_dane/speeches.csv", sep='|')

C:\Users\Mag\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2698: DtypeWarning: Columns (3,14) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


## 1. Znalezienie imienia i nazwiska przemawiającego

In [5]:
speeches['author'] = speeches['speech_raw'].apply(funcs.name_finder)

Zapisanie rozszerzonych danych do dalszych analiz.

In [5]:
speeches.to_csv('00_dane/speeches.csv', encoding='UTF=8')

## 2. Wczytanie danych po czyszczeniu SQL i dodaniu autora

In [45]:
politicians = pd.read_csv("00_dane/portraits.csv", sep='|')
speeches = pd.read_csv("00_dane/speeches.csv", sep='|')

#speeches.to_csv('00_dane/speeches_2.csv', encoding='UTF=8')

C:\Users\Mag\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2698: DtypeWarning: Columns (3,14) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [46]:
len(speeches['speech_raw']), sum(1-pd.isnull(speeches['author_final']))


(272221, 225388)

Czyszczenie znaków specjalnych i wycinanie nagłówka.

In [50]:
start = timer()
speeches['speech_raw'] = speeches['speech_raw'].apply(funcs.rem_head)
speeches['speech_raw'] = speeches['speech_raw'].apply(funcs.clear_text)
speeches['speech_title'] = speeches['speech_title'].apply(funcs.clear_text)
end = timer()
print(end - start)

199.21203914773992


Wycinam fragment, który jest tytułem:
1. Dodaję "\" przed nawiasami w tytule.
2. Wycinam tytuł z treści.

In [59]:
start = timer()
speeches['speech_title'] = speeches['speech_title'].apply(lambda t: re.sub('\(','\(',t))
speeches['speech_title'] = speeches['speech_title'].apply(lambda t: re.sub('\)','\)',t))
print(timedelta(seconds=timer()-start))

0:00:02.033795


In [65]:
sum(pd.isnull(speeches['speech_title']))

0

In [68]:
for t, r, in zip(speeches['speech_title'], speeches['speech_raw']):
    print('a'+ t)
    print('r'+r)
    print(re.sub(t, '', r) )

aSprawozdanie Komisji Polityki Gospodarczej, Budżetu i Finansów o rządowym projekcie ustawy o podatku importowym od towarów sprowadzanych lub nadsyłanych z zagranicy oraz o zmianie ustawy o podatku od towarów i usług oraz o podatku akcyzowym \(druki nr 882 i 918\).
r Sprawozdanie Komisji Polityki Gospodarczej, Budżetu i Finansów o rządowym projekcie ustawy o podatku importowym od towarów sprowadzanych lub nadsyłanych z zagranicy oraz o zmianie ustawy o podatku od towarów i usług oraz o podatku akcyzowym (druki nr 882 i 918). Poseł Paweł Abramski: Panie Marszałku! Wysoka Izbo! Rozporządzenie ministra finansów o podwyższeniu o 6% granicznego podatku importowego wprowadzone zostało w życie - jak mówił pan poseł sprawozdawca - w dniu 17 grudnia 1992 r. Podwyższenie tego podatku zostało równocześnie notyfikowane przez Polskę w GATT jako rozwiązanie, które ma pomóc w uporaniu się z trudnościami w bilansach płatniczych stosownie do postanowień art. 12/4 Układu Ogólnego w Sprawie Ceł i Handlu.

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.



aInterpelacje i zapytania.
r Interpelacje i zapytania. Poseł Ryszard Jacek Żochowski: Całkowicie przekonała mnie odpowiedź pana ministra i nie mam dodatkowych pytań. Mam nadzieję, że te praktyki, które były poprzednio, nie będą więcej stosowane. Jeżeli chodzi o przejęzyczenie, domyślałem się, że zaszło nieporozumienie, bo nie wierzyłem, żeby ministerstwo miało taki fundusz specjalny.
  Poseł Ryszard Jacek Żochowski: Całkowicie przekonała mnie odpowiedź pana ministra i nie mam dodatkowych pytań. Mam nadzieję, że te praktyki, które były poprzednio, nie będą więcej stosowane. Jeżeli chodzi o przejęzyczenie, domyślałem się, że zaszło nieporozumienie, bo nie wierzyłem, żeby ministerstwo miało taki fundusz specjalny.
apoza punktami porządku
rPoseł Ryszard Jacek Żochowski: Panie Marszałku! Wysoka Izbo! 12 lutego skierowałem, zgodnie z art. 64, 65 i 67 tymczasowego regulaminu Sejmu, pytanie do prezesa Rady Ministrów w sprawie tragicznej sytuacji przemysłu farmaceutycznego. Ostatnie dwa tygodn

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.



r 9. Sprawozdania Komisji Samorządu Terytorialnego oraz Komisji Ustawodawczej o poselskich projektach ustaw o zmianie ustawy Przepisy wprowadzające ustawę o samorządzie terytorialnym i ustawę o pracownikach samorządowych (druki nr 308, 416, 899 i 1335). 10. Sprawozdanie Komisji Polityki Przestrzennej, Budowlanej i Mieszkaniowej, Komisji Samorządu Terytorialnego oraz Komisji Ustawodawczej o rządowym projekcie ustawy o zmianie ustawy Przepisy wprowadzające ustawę o samorządzie terytorialnym i ustawę o pracownikach samorządowych (druki nr 1117 i 1332). Poseł Jerzy Jankowski: Pani Marszałek! Wysoka Izbo! Przedłożone sprawozdanie trzech połączonych komisji sejmowych o projekcie ustawy jest realizacją orzeczenia Trybunału Konstytucyjnego z dnia 12 października 1993 r., uznającego za niezgodny z konstytucją art. 36 ustawy Przepisy wprowadzające ustawę o samorządzie terytorialnym i ustawę o pracownikach samorządowych. Wysoka Izbo! Na podstawie zakwestionowanego art. 36 wymienionej ustawy z dn

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


TypeError: must be str, not NoneType

In [61]:
speeches['speech_raw'] = [re.sub(t, '', r) for t, r, in zip(speeches['speech_title'], speeches['speech_raw'])] 
#a = 'Pierwsze czytanie poselskiego projektu ustawy o likwidacji Instytutu Pamięci Narodowej - Komisji Ścigania Zbrodni przeciwko Narodowi Polskiemu \(druk'
#print(a)
#print(b)
#re.sub(a, '', b)

TypeError: expected string or bytes-like object

In [28]:
start = timer()
speeches['speech_title'] = speeches['speech_title'].apply(lambda t: re.sub('\(','\(',t))
speeches['speech_title'] = speeches['speech_title'].apply(lambda t: re.sub('\)','\)',t))
print(timedelta(seconds=timer()-start))

0:00:02.010682


In [33]:
speeches['speech_title'] = speeches['speech_title'].apply(lambda t: re.sub('[\\]+','',t))

error: unterminated character set at position 0

In [29]:
a , b = speeches['speech_title'].iloc[105], speeches['speech_raw'].iloc[105]
#a = 'Pierwsze czytanie poselskiego projektu ustawy o likwidacji Instytutu Pamięci Narodowej - Komisji Ścigania Zbrodni przeciwko Narodowi Polskiemu \(druk'
print(a)
print(b)
#re.sub(a, '', b)

Informacja o skutkach ostatnich podwyżek cen energii elektrycznej, gazu i centralnego ogrzewania dla budżetu państwa oraz spodziewanym wzroście kosztów utrzymania i planowanych rekompensatach dla najbardziej potrzebujących oraz sprawozdanie Komisji Polityki Gospodarczej, Budżetu i Finansów o projekcie oświadczenia w sprawie podwyżek cen nośników energii \\\\(druki nr 49 i 67\\\\).
 Informacja o skutkach ostatnich podwyżek cen energii elektrycznej, gazu i centralnego ogrzewania dla budżetu państwa oraz spodziewanym wzroście kosztów utrzymania i planowanych rekompensatach dla najbardziej potrzebujących oraz sprawozdanie Komisji Polityki Gospodarczej, Budżetu i Finansów o projekcie oświadczenia w sprawie podwyżek cen nośników energii (druki nr 49 i 67). Poseł Władysław Adamski: Panie Marszałku! Wysoki Sejmie! Jako poseł o rodowodzie związkowym z dużą uwagą wysłuchałem przedstawionych nam informacji. Jako poseł z ramienia OPZZ nie mogę też inaczej niż nagannie ocenić sposobu, w jaki został

In [20]:
speeches.to_csv('00_dane/speeches_2.csv', encoding='UTF=8')

In [16]:
speeches.head(10)

field1  term                                      id_ session_number  day_  \
0       0     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             45     1   
1       1     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             44     1   
2       2     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             42     1   
3       3     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             40     4   
4       4     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             39     4   
5       5     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             39     4   
6       6     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             38     4   
7       7     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             36     2   
8       8     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             36     2   
9       9     1  (1, 'e7324c1b0d486d77c1256815004bf61e')             35     4   

        date_ number_                                       speech_title  \
0  27-05-1993       4  Sprawozdanie Komisji Polityki Gospodarczej, Bu...   
1  13-05-1993       2  Sprawozdanie Komisji Sprawiedliwości oraz Komi...   
2  15-04-1993       4  Sprawozdanie Komisji Stosunków Gospodarczych z...   
3  31-03-1993      12  Stanowisko rządu w sprawie daleko idących rozb...   
4  17-03-1993      12  Informacja rządu o sposobie wykonania uchwały ...   
5  17-03-1993      12  Informacja rządu o sposobie wykonania uchwały ...   
6  03-03-1993      18  Informacja rządu o działaniach podejmowanych p...   
7  05-02-1993       7                          Interpelacje i zapytania.   
8  05-02-1993       7                          Interpelacje i zapytania.   
9  03-02-1993      19  Pierwsze czytanie senackiego projektu ustawy o...   

  speech_number                                        speech_link  \
0          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   
1          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   
2          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   
3          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   
4          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   
5          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   
6          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   
7          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   
8          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   
9          None  /Debata1.nsf/5c30b337b5bc240ec125746d0030d0fc/...   

                                          speech_raw     db_date  \
0   Sprawozdanie Komisji Polityki Gospodarczej, B...  2019-05-04   
1   Sprawozdanie Komisji Sprawiedliwości oraz Kom...  2019-05-04   
2   Sprawozdanie Komisji Stosunków Gospodarczych ...  2019-05-04   
3   Stanowisko rządu w sprawie daleko idących roz...  2019-05-04   
4   Informacja rządu o sposobie wykonania uchwały...  2019-05-04   
5   Informacja rządu o sposobie wykonania uchwały...  2019-05-04   
6   Informacja rządu o działaniach podejmowanych ...  2019-05-04   
7   Interpelacje i zapytania. Poseł Paweł Abramsk...  2019-05-04   
8   Interpelacje i zapytania. Poseł Paweł Abramsk...  2019-05-04   
9   Pierwsze czytanie senackiego projektu ustawy ...  2019-05-04   

     author_by_id  author_by_text    author_final  
0  Paweł Abramski  Paweł Abramski  Paweł Abramski  
1  Paweł Abramski  Paweł Abramski  Paweł Abramski  
2  Paweł Abramski  Paweł Abramski  Paweł Abramski  
3  Paweł Abramski  Paweł Abramski  Paweł Abramski  
4  Paweł Abramski  Paweł Abramski  Paweł Abramski  
5  Paweł Abramski  Paweł Abramski  Paweł Abramski  
6  Paweł Abramski  Paweł Abramski  Paweł Abramski  
7  Paweł Abramski             NaN  Paweł Abramski  
8  Paweł Abramski  Paweł Abramski  Paweł Abramski  
9  Paweł Abramski  Paweł Abramski  Paweł Abramski